In [7]:
import os 
import import_ipynb
import pandas as pd
from shapely.geometry import Point
from shapely.geometry.polygon import Polygon
from shapely.ops import unary_union
from geopy.distance import geodesic
import geopandas as gpd

In [8]:
filename = ('C:\\Users\\ruthv\\OneDrive\\Documents\\BTTMarsh\\BTT---Marsh\\Work\\merged_vessel_hurricane_101624.csv')
vessel_df = pd.read_csv(filename)

In [9]:
vessel_df.head()

Unnamed: 0_x       MMSI         BaseDateTime       LAT        LON   SOG  \
0         46570  249819000  2023-09-22 00:00:00  24.42413 -114.17018  18.5   
1         46570  249819000  2023-09-22 00:00:00  24.42413 -114.17018  18.5   
2         46571  538007439  2023-09-22 00:00:00  25.19859  -80.09527  16.3   
3         46571  538007439  2023-09-22 00:00:00  25.19859  -80.09527  16.3   
4         46572  563066900  2023-09-22 00:00:00  32.85378  -78.79110  20.1   

     COG  Heading     VesselName         IMO  ... 34-knot Wind Radii NW  \
0  121.6      121  CMA CGM LIBRA  IMO9399193  ...                 110.0   
1  121.6      121  CMA CGM LIBRA  IMO9399193  ...                 180.0   
2  201.2      202     GLOVIS SKY  IMO9798404  ...                 110.0   
3  201.2      202     GLOVIS SKY  IMO9798404  ...                 180.0   
4  231.2      231   POLAR MEXICO  IMO9786750  ...                 110.0   

   50-knot Wind Radii NE  50-knot Wind Radii SE  50-knot Wind Radii SW  \
0                  100.0                  110.0                   80.0   
1                    0.0                    0.0                    0.0   
2                  100.0                  110.0                   80.0   
3                    0.0                    0.0                    0.0   
4                  100.0                  110.0                   80.0   

   50-knot Wind Radii NW  64-knot Wind Radii NE  64-knot Wind Radii SE  \
0                   60.0                   60.0                   60.0   
1                    0.0                    0.0                    0.0   
2                   60.0                   60.0                   60.0   
3                    0.0                    0.0                    0.0   
4                   60.0                   60.0                   60.0   

  64-knot Wind Radii SW  64-knot Wind Radii NW   hurricane_datetime  
0                  40.0                   30.0  2023-09-22 00:00:00  
1                   0.0                    0.0  2023-09-22 00:00:00  
2                  40.0                   30.0  2023-09-22 00:00:00  
3                   0.0                    0.0  2023-09-22 00:00:00  
4                  40.0                   30.0  2023-09-22 00:00:00  

[5 rows x 42 columns]

In [10]:
vessel_df['Date_only'] = pd.to_datetime(vessel_df['BaseDateTime'], errors='coerce')

In [11]:
vessel_df.columns

Index(['Unnamed: 0_x', 'MMSI', 'BaseDateTime', 'LAT', 'LON', 'SOG', 'COG',
       'Heading', 'VesselName', 'IMO', 'CallSign', 'VesselType', 'Status',
       'Length', 'Width', 'Draft', 'Cargo', 'TransceiverClass', 'Unnamed: 0_y',
       'Name', 'Num Entries', 'Year', 'Time', 'Record Identifier',
       'Status of System', 'Latitude', 'Longitude', 'Maximum Sustained Wind',
       'Minimum Pressure', '34-knot Wind Radii NE', '34-knot Wind Radii SE',
       '34-knot Wind Radii SW', '34-knot Wind Radii NW',
       '50-knot Wind Radii NE', '50-knot Wind Radii SE',
       '50-knot Wind Radii SW', '50-knot Wind Radii NW',
       '64-knot Wind Radii NE', '64-knot Wind Radii SE',
       '64-knot Wind Radii SW', '64-knot Wind Radii NW', 'hurricane_datetime',
       'Date_only'],
      dtype='object')

In [12]:
def convert_to_decimal_degrees(coord_str):
    
    if pd.isna(coord_str) or not isinstance(coord_str, str):
        return None
    
    try:
        value, direction = coord_str[:-1], coord_str[-1]
        value = float(value)
        if direction in ['S', 'W']:
            value = -value
        return value
    except ValueError:
        return None
    

# sample/testing
sample_coords = ['28.8N', '56.4W']
print([convert_to_decimal_degrees(coord) for coord in sample_coords])

[28.8, -56.4]


In [13]:
vessel_df['Latitude'] = vessel_df['Latitude'].apply(convert_to_decimal_degrees)
vessel_df['Longitude'] = vessel_df['Longitude'].apply(convert_to_decimal_degrees)

In [ ]:
def identify_impacted_vessels(vessel_df):
    '''
    This function first maps hurricanes to a radius in kilometers determined by the max_wind_speed column. The radius are determined by the Saffir-Simpson Scale. 
    https://en.wikipedia.org/wiki/Saffir%E2%80%93Simpson_scale
    A category does not have a fixed diameter or size, so I used PerplexityAi to give me
    adequate measurement for each category.
    Still, the size of hurricanes varies dramatically. The effect of hurricanes on ports
    and ships would more depend on its wind speed. Currently, the function is only testing on whether 
    the vessel is in the radius that I have set, which assumes the hurricanes diameter,-
    not if it is damaged. 
    '''

    def calculate_radius(max_wind_speed):
        if max_wind_speed >= 137:  
            return 161  # Radius in kilometers for Category 5 hurricanes
        elif max_wind_speed >= 113:  
            return 161  # Radius in kilometers for Category 4 hurricanes
        elif max_wind_speed >= 96:  
            return 161  # Radius in kilometers for Category 3 hurricanes
        elif max_wind_speed >= 83:  
            return 100  # Radius in kilometers for Category 2 hurricanes
        elif max_wind_speed >= 64:  
            return 100  # Radius in kilometers for Category 1 hurricanes
        elif max_wind_speed >= 34:
            return 50
        else:
            return 0  
    
    vessel_df['impacted'] = False  

    #Processed_timestamps is to make sure that we only iterate through the hurricane_datetime once in the for loop

    processed_timestamps = set()

    print(vessel_df[['Latitude', 'Longitude']].head())

    for idx, hurricane in vessel_df.iterrows():
        hurricane_lat = hurricane['Latitude']
        hurricane_lon = hurricane['Longitude']
        hurricane_time = hurricane['hurricane_datetime']
        max_wind_speed = hurricane['Maximum Sustained Wind'] 

        if pd.isna(hurricane_lat) or pd.isna(hurricane_lon) or pd.isna(max_wind_speed):
            continue 
        if hurricane_time in processed_timestamps:
            continue
        processed_timestamps.add(hurricane_time)

        impact_radius = calculate_radius(max_wind_speed)
        if impact_radius == 0:
            continue  

        hurricane_point = Point(hurricane_lon, hurricane_lat)

        matching_vessels = vessel_df[vessel_df['BaseDateTime'] == hurricane_time]
        
        if matching_vessels.empty:
            # print(matching_vessels)
            print(f"No vessels found for hurricane time: {hurricane_time}")
            continue
        
        print(f"{len(matching_vessels)} vessels found for hurricane at {hurricane_time}")


        for v_idx, vessel in matching_vessels.iterrows():
            vessel_lat = vessel['LAT']
            vessel_lon = vessel['LON']
            
            if pd.isna(vessel_lat) or pd.isna(vessel_lon):
                continue  

            distance = geodesic((vessel_lat, vessel_lon), (hurricane_lat, hurricane_lon)).kilometers

            print(f"Vessel at ({vessel_lat}, {vessel_lon}) - Distance: {distance:.2f} km from hurricane on {hurricane_time}")

            if distance <= impact_radius:
                # Mark the vessel as impacted
                vessel_df.at[v_idx, 'impacted'] = True
                vessel_id = vessel.get('vessel_id', 'Unknown ID')
                print(f"Vessel {vessel_id} is impacted.")

    return vessel_df  

In [15]:
def process_weeks_with_impact(vessel_df):
    start_date = '2023-09-01' 
    end_date = '2023-09-30'

    # storing the results of each week
    all_weeks_data = []

    # Iterate week by week
    for week_start in pd.date_range(start=start_date, end=end_date, freq='W-MON'):
        week_end = week_start + pd.Timedelta(days=6)

        # Filter the dataset for the current week (using only the date part)
        vessel_week = vessel_df[(vessel_df['Date_only'] >= week_start) & (vessel_df['Date_only'] <= week_end)]
        
        # Process the hurricane and vessel data for this week
        if not vessel_week.empty:
            print(f"Processing week starting {week_start.date()} with hurricanes and {len(vessel_week)} vessels")
            
            impacted_vessels_week = identify_impacted_vessels(vessel_week)

            # Append the impacted vessel data for this week to the list
            all_weeks_data.append(impacted_vessels_week)

    # Concatenate all processed week data into a single DataFrame
    final_df = pd.concat(all_weeks_data, ignore_index=True)

    return final_df

In [16]:
processed_vessel_df = process_weeks_with_impact(vessel_df)

Processing week starting 2023-09-04 with hurricanes and 39251 vessels
      Latitude  Longitude
7487      46.3      -19.1
7488      19.6      -40.9
7489      19.0      -56.0
7490      19.1      -35.1
7491      46.3      -19.1


C:\Users\ruthv\AppData\Local\Temp\ipykernel_46164\2272647759.py:30: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  vessel_df['impacted'] = False


2215 vessels found for hurricane at 2023-09-08 00:00:00
Vessel at (40.50571, -71.97616) - Distance: 4348.91 km from hurricane on 2023-09-08 00:00:00
Vessel at (40.50571, -71.97616) - Distance: 4348.91 km from hurricane on 2023-09-08 00:00:00
Vessel at (40.50571, -71.97616) - Distance: 4348.91 km from hurricane on 2023-09-08 00:00:00
Vessel at (40.50571, -71.97616) - Distance: 4348.91 km from hurricane on 2023-09-08 00:00:00
Vessel at (40.50571, -71.97616) - Distance: 4348.91 km from hurricane on 2023-09-08 00:00:00
Vessel at (47.45509, -89.83734) - Distance: 5211.03 km from hurricane on 2023-09-08 00:00:00
Vessel at (47.45509, -89.83734) - Distance: 5211.03 km from hurricane on 2023-09-08 00:00:00
Vessel at (47.45509, -89.83734) - Distance: 5211.03 km from hurricane on 2023-09-08 00:00:00
Vessel at (47.45509, -89.83734) - Distance: 5211.03 km from hurricane on 2023-09-08 00:00:00
Vessel at (47.45509, -89.83734) - Distance: 5211.03 km from hurricane on 2023-09-08 00:00:00
Vessel at (31.

C:\Users\ruthv\AppData\Local\Temp\ipykernel_46164\2272647759.py:30: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  vessel_df['impacted'] = False


Vessel at (42.73035, -79.44238) - Distance: 1088.09 km from hurricane on 2023-09-17 00:00:00
Vessel at (42.73035, -79.44238) - Distance: 1088.09 km from hurricane on 2023-09-17 00:00:00
Vessel at (36.31283, -122.41745) - Distance: 4758.29 km from hurricane on 2023-09-17 00:00:00
Vessel at (36.31283, -122.41745) - Distance: 4758.29 km from hurricane on 2023-09-17 00:00:00
Vessel at (36.31283, -122.41745) - Distance: 4758.29 km from hurricane on 2023-09-17 00:00:00
Vessel at (30.04403, -90.68042) - Distance: 2692.62 km from hurricane on 2023-09-17 00:00:00
Vessel at (30.04403, -90.68042) - Distance: 2692.62 km from hurricane on 2023-09-17 00:00:00
Vessel at (30.04403, -90.68042) - Distance: 2692.62 km from hurricane on 2023-09-17 00:00:00
Vessel at (26.09362, -80.1016) - Distance: 2412.16 km from hurricane on 2023-09-17 00:00:00
Vessel at (26.09362, -80.1016) - Distance: 2412.16 km from hurricane on 2023-09-17 00:00:00
Vessel at (26.09362, -80.1016) - Distance: 2412.16 km from hurricane 

C:\Users\ruthv\AppData\Local\Temp\ipykernel_46164\2272647759.py:30: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  vessel_df['impacted'] = False


Vessel at (49.02332, -123.14745) - Distance: 6140.04 km from hurricane on 2023-09-22 00:00:00
Vessel at (49.02332, -123.14745) - Distance: 6140.04 km from hurricane on 2023-09-22 00:00:00
Vessel at (49.01516, -123.15518) - Distance: 6140.98 km from hurricane on 2023-09-22 00:00:00
Vessel at (49.01516, -123.15518) - Distance: 6140.98 km from hurricane on 2023-09-22 00:00:00
Vessel at (26.51241, -95.00482) - Distance: 5363.81 km from hurricane on 2023-09-22 00:00:00
Vessel at (26.51241, -95.00482) - Distance: 5363.81 km from hurricane on 2023-09-22 00:00:00
Vessel at (31.89378, -80.46465) - Distance: 3864.58 km from hurricane on 2023-09-22 00:00:00
Vessel at (31.89378, -80.46465) - Distance: 3864.58 km from hurricane on 2023-09-22 00:00:00
Vessel at (31.92411, -80.53095) - Distance: 3868.00 km from hurricane on 2023-09-22 00:00:00
Vessel at (31.92411, -80.53095) - Distance: 3868.00 km from hurricane on 2023-09-22 00:00:00
Vessel at (46.58013, -87.38931) - Distance: 3756.99 km from hurric

C:\Users\ruthv\AppData\Local\Temp\ipykernel_46164\2272647759.py:30: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  vessel_df['impacted'] = False


Vessel at (28.40999, -80.60784) - Distance: 2812.09 km from hurricane on 2023-09-30 00:00:00
Vessel at (28.40999, -80.60784) - Distance: 2812.09 km from hurricane on 2023-09-30 00:00:00
Vessel at (32.78846, -79.9176) - Distance: 2952.02 km from hurricane on 2023-09-30 00:00:00
Vessel at (32.78846, -79.9176) - Distance: 2952.02 km from hurricane on 2023-09-30 00:00:00
Vessel at (36.95128, -76.024) - Distance: 2927.31 km from hurricane on 2023-09-30 00:00:00
Vessel at (36.95128, -76.024) - Distance: 2927.31 km from hurricane on 2023-09-30 00:00:00
Vessel at (36.95343, -75.16804) - Distance: 2871.13 km from hurricane on 2023-09-30 00:00:00
Vessel at (36.95343, -75.16804) - Distance: 2871.13 km from hurricane on 2023-09-30 00:00:00
Vessel at (38.47307, -74.04358) - Distance: 2920.85 km from hurricane on 2023-09-30 00:00:00
Vessel at (38.47307, -74.04358) - Distance: 2920.85 km from hurricane on 2023-09-30 00:00:00
Vessel at (23.46929, -82.48887) - Distance: 2863.56 km from hurricane on 202